In [1]:
import pandas as pd

In [2]:
data = pd.read_pickle("../data/df.pickle") # "data/df.pickle"

In [3]:
pd.set_option('display.max_columns', None)

In [4]:
data.head()

uniform_id lang itemid  sentnum  ianum      ia  skip        TF        FP  \
0       ee_1   ee      1      1.0    1.0  Samuel   0.0  0.059849  0.059849   
1       ee_1   ee      1      1.0    2.0  Morse,   0.0  0.044309  0.044309   
2       ee_1   ee      1      1.0    3.0    best   1.0  0.000000  0.000000   
3       ee_1   ee      1      1.0    4.0   known   0.0  0.043049  0.043049   
4       ee_1   ee      1      1.0    5.0   today   0.0  0.045359  0.045359   

         FF          ia_id  
0  0.023100  1_0001_Samuel  
1  0.044309  1_0002_Morse,  
2  0.000000    1_0003_best  
3  0.043049   1_0004_known  
4  0.045359   1_0005_today

## Get unigrams based on data from one language
## Use unigrams to generate bigrams and trigrams

In [5]:
languages = data['lang'].unique()

In [6]:
languages

array(['ee', 'fi', 'ge', 'he', 'it', 'en', 'sp'], dtype=object)

In [7]:
lang_dict = {elem : pd.DataFrame() for elem in languages}

for key in lang_dict.keys():
    lang_dict[key] = data[:][data.lang == key]

In [8]:
unigrams = sorted(set(lang_dict['fi']['ia_id']))

In [9]:
text = " ".join(sorted(set(lang_dict['fi']['ia_id'])))

In [10]:
bigrams = [b for b in zip(unigrams[:-1], unigrams[1:])]

In [11]:
bigrams[:5]

[('1_0001_Samuel', '1_0002_Morse,'),
 ('1_0002_Morse,', '1_0003_best'),
 ('1_0003_best', '1_0004_known'),
 ('1_0004_known', '1_0005_today'),
 ('1_0005_today', '1_0006_as')]

In [12]:
trigrams = [t for t in zip(unigrams[:-2], unigrams[1:-1], unigrams[2:])]

In [13]:
trigrams[:5]

[('1_0001_Samuel', '1_0002_Morse,', '1_0003_best'),
 ('1_0002_Morse,', '1_0003_best', '1_0004_known'),
 ('1_0003_best', '1_0004_known', '1_0005_today'),
 ('1_0004_known', '1_0005_today', '1_0006_as'),
 ('1_0005_today', '1_0006_as', '1_0007_the')]

## Get tags

In [38]:
tags = pd.read_pickle("../data/df_tags.pickle")
POS_mapper = pd.Series(tags.POS_tag.values, index=tags.ia_id).to_dict()
PTB_mapper = pd.Series(tags.PTB_tag.values, index=tags.ia_id).to_dict()
UD_mapper = pd.Series(tags.UD_tag.values, index=tags.ia_id).to_dict()

In [118]:
def map_bigrams(df, mapper):
    df = df.reset_index()
    df = pd.melt(df, id_vars="uniform_id", value_vars = df.columns)
    df.variable = df.variable.apply(lambda x: (mapper[x.split(":")[0]], mapper[x.split(":")[1]]))
    df = pd.pivot_table(df, values="value", index="uniform_id", columns="variable")
    return df

def map_trigrams(df, mapper):
    df = df.reset_index()
    df = pd.melt(df, id_vars="uniform_id", value_vars = df.columns)
    df.variable = df.variable.apply(lambda x: (mapper[x.split(":")[0]], mapper[x.split(":")[1]], mapper[x.split(":")[2]]))
    df = pd.pivot_table(df, values="value", index="uniform_id", columns="variable")
    return df

## Use pivoted data to get values for bigrams and trigrams

In [101]:
data_pivoted = pd.read_pickle("../data/df_pivoted.pickle") # "data/df_pivoted.pickle"

In [102]:
data_pivoted['TF'].head()

ia_id       1_0001_Samuel  1_0002_Morse,  1_0003_best  1_0004_known  \
uniform_id                                                            
ee_1             0.059849       0.044309     0.000000      0.043049   
ee_16            0.011184       0.080913     0.000000      0.032350   
ee_17            0.093407       0.174359     0.000000      0.097070   
ee_19            0.072944       0.062334     0.065539      0.038904   
ee_2             0.055410       0.071429     0.029421      0.038411   

ia_id       1_0005_today  1_0006_as  1_0007_the  1_0008_inventor  1_0009_of  \
uniform_id                                                                    
ee_1            0.045359   0.000000    0.049769         0.043679   0.028139   
ee_16           0.012084   0.012009    0.024469         0.046386   0.000000   
ee_17           0.000000   0.102564    0.000000         0.021978   0.061172   
ee_19           0.057250   0.035146    0.052940         0.040893   0.018015   
ee_2            0.049689   0.028114    0.000000         0.081890   0.000000   

ia_id       1_0010_Morse  1_0011_Code  1_0012_and  1_0013_one  1_0014_of  \
uniform_id                                                                 
ee_1            0.041789     0.000000    0.040739    0.049349   0.000000   
ee_16           0.052616     0.037079    0.022367    0.015012   0.000000   
ee_17           0.000000     0.082051    0.000000    0.000000   0.052747   
ee_19           0.069297     0.085875    0.000000    0.010942   0.000000   
ee_2            0.043969     0.062439    0.000000    0.000000   0.000000   

ia_id       1_0015_the  1_0016_inventors  1_0017_of  1_0018_the  \
uniform_id                                                        
ee_1          0.039899          0.034649   0.039689    0.049139   
ee_16         0.016138          0.098401   0.015762    0.035427   
ee_17         0.000000          0.054579   0.000000    0.000000   
ee_19         0.016468          0.034151   0.015363    0.000000   
ee_2          0.050997          0.097581   0.000000    0.024845   

ia_id       1_0019_telegraph,  1_0020_was  1_0021_originally  1_0022_a  \
uniform_id                                                               
ee_1                 0.051029    0.019110           0.062789  0.000000   
ee_16                0.262929    0.034302           0.029873  0.009532   
ee_17                0.049817    0.000000           0.089011  0.000000   
ee_19                0.034593    0.021662           0.080349  0.000000   
ee_2                 0.053449    0.114090           0.074534  0.000000   

ia_id       1_0023_prominent  1_0024_painter.  1_0025_While  1_0026_he  \
uniform_id                                                               
ee_1                0.143847         0.113818      0.040170   0.015013   
ee_16               0.065901         0.085266      0.022401   0.013286   
ee_17               0.121245         0.000000      0.030585   0.000000   
ee_19               0.115385         0.071950      0.051067   0.006286   
ee_2                0.059660         0.064073      0.000000   0.018334   

ia_id       1_0027_was  1_0028_always  1_0029_interested  1_0030_in  \
uniform_id                                                            
ee_1          0.102252       0.081152           0.063806   0.000000   
ee_16         0.010783       0.009771           0.060054   0.011379   
ee_17         0.037234       0.000000           0.035461   0.000000   
ee_19         0.040048       0.015327           0.031996   0.000000   
ee_2          0.000000       0.020200           0.018334   0.000000   

ia_id       1_0031_technology  1_0032_and  1_0033_studied  1_0034_electrical  \
uniform_id                                                                     
ee_1                 0.046054    0.000000        0.044938           0.025462   
ee_16                0.094310    0.015252        0.049926           0.052845   
ee_17                0.036348    0.000000        0.041888           0.092420   
ee_19    

In [110]:
tf_dict = {}
fp_dict = {}
ff_dict = {}
for bigram in bigrams:
    bigram_str = ":".join(bigram)
    tf_dict[bigram_str] = data_pivoted['TF'][bigram[0]]+data_pivoted['TF'][bigram[1]]
    fp_dict[bigram_str] = data_pivoted['FP'][bigram[0]]+data_pivoted['FP'][bigram[1]]
    ff_dict[bigram_str] = data_pivoted['FF'][bigram[0]]+data_pivoted['FF'][bigram[1]]

In [111]:
## Dataframes with bigrams (separately for TF, FP and FF)
data_tf_bigrams = pd.DataFrame.from_dict(tf_dict)
data_fp_bigrams = pd.DataFrame.from_dict(fp_dict)
data_ff_bigrams = pd.DataFrame.from_dict(ff_dict)

In [112]:
data_tf_bigrams.head(5)

1_0001_Samuel:1_0002_Morse,  1_0002_Morse,:1_0003_best  \
uniform_id                                                           
ee_1                           0.104158                   0.044309   
ee_16                          0.092096                   0.080913   
ee_17                          0.267766                   0.174359   
ee_19                          0.135279                   0.127874   
ee_2                           0.126839                   0.100850   

            1_0003_best:1_0004_known  1_0004_known:1_0005_today  \
uniform_id                                                        
ee_1                        0.043049                   0.088408   
ee_16                       0.032350                   0.044434   
ee_17                       0.097070                   0.097070   
ee_19                       0.104443                   0.096154   
ee_2                        0.067833                   0.088101   

            1_0005_today:1_0006_as  1_0006_as:1_0007_the  \
uniform_id                                                 
ee_1                      0.045359              0.049769   
ee_16                     0.024094              0.036478   
ee_17                     0.102564              0.102564   
ee_19                     0.092396              0.088086   
ee_2                      0.077803              0.028114   

            1_0007_the:1_0008_inventor  1_0008_inventor:1_0009_of  \
uniform_id                                                          
ee_1                          0.093448                   0.071819   
ee_16                         0.070855                   0.046386   
ee_17                         0.021978                   0.083150   
ee_19                         0.093833                   0.058908   
ee_2                          0.081890                   0.081890   

            1_0009_of:1_0010_Morse  1_0010_Morse:1_0011_Code  \
uniform_id                                                     
ee_1                      0.069929                  0.041789   
ee_16                     0.052616                  0.089695   
ee_17                     0.061172                  0.082051   
ee_19                     0.087312                  0.155172   
ee_2                      0.043969                  0.106407   

            1_0011_Code:1_0012_and  1_0012_and:1_0013_one  \
uniform_id                                                  
ee_1                      0.040739               0.090088   
ee_16                     0.059446               0.037379   
ee_17                     0.082051               0.000000   
ee_19                     0.085875               0.010942   
ee_2                      0.062439               0.000000   

            1_0013_one:1_0014_of  1_0014_of:1_0015_the  \
uniform_id                                               
ee_1                    0.049349              0.039899   
ee_16                   0.015012              0.016138   
ee_17                   0.052747              0.052747   
ee_19                   0.010942              0.016468   
ee_2                    0.000000              0.050997   

            1_0015_the:1_0016_inventors  1_0016_inventors:1_0017_of  \
uniform_id                                                            
ee_1                           0.074549                    0.074339   
ee_16                          0.114539                    0.114163   
ee_17                          0.054579                    0.054579   
ee_19                          0.050619                    0.049514   
ee_2                           0.148578                    0.097581   

            1_0017_of:1_0018_the  1_0018_the:1_0019_telegraph,  \
uniform_id                                                       
ee_1                    0.088828                      0.100168   
ee_16                   0.051190                      0.298356   
ee_17                   0.000000                      0.049817   
ee_19                   0.015363  

In [113]:
tf_dict_trigrams = {}
fp_dict_trigrams = {}
ff_dict_trigrams = {}
for trigram in trigrams:
    trigram_str = ":".join(trigram)
    tf_dict_trigrams[trigram_str] = data_pivoted['TF'][trigram[0]]+data_pivoted['TF'][trigram[1]]+data_pivoted['TF'][trigram[2]]
    fp_dict_trigrams[trigram_str] = data_pivoted['FP'][trigram[0]]+data_pivoted['FP'][trigram[1]]+data_pivoted['FP'][trigram[2]]
    ff_dict_trigrams[trigram_str] = data_pivoted['FF'][trigram[0]]+data_pivoted['FF'][trigram[1]]+data_pivoted['FF'][trigram[2]]

In [114]:
## Dataframes with trigrams (separately for TF, FP and FF)
data_tf_trigrams = pd.DataFrame.from_dict(tf_dict_trigrams)
data_fp_trigrams = pd.DataFrame.from_dict(fp_dict_trigrams)
data_ff_trigrams = pd.DataFrame.from_dict(ff_dict_trigrams)

In [115]:
data_tf_trigrams.head()

1_0001_Samuel:1_0002_Morse,:1_0003_best  \
uniform_id                                            
ee_1                                       0.104158   
ee_16                                      0.092096   
ee_17                                      0.267766   
ee_19                                      0.200818   
ee_2                                       0.156260   

            1_0002_Morse,:1_0003_best:1_0004_known  \
uniform_id                                           
ee_1                                      0.087358   
ee_16                                     0.113263   
ee_17                                     0.271429   
ee_19                                     0.166777   
ee_2                                      0.139261   

            1_0003_best:1_0004_known:1_0005_today  \
uniform_id                                          
ee_1                                     0.088408   
ee_16                                    0.044434   
ee_17                                    0.097070   
ee_19                                    0.161693   
ee_2                                     0.117522   

            1_0004_known:1_0005_today:1_0006_as  \
uniform_id                                        
ee_1                                   0.088408   
ee_16                                  0.056444   
ee_17                                  0.199634   
ee_19                                  0.131300   
ee_2                                   0.116214   

            1_0005_today:1_0006_as:1_0007_the  \
uniform_id                                      
ee_1                                 0.095128   
ee_16                                0.048563   
ee_17                                0.102564   
ee_19                                0.145336   
ee_2                                 0.077803   

            1_0006_as:1_0007_the:1_0008_inventor  \
uniform_id                                         
ee_1                                    0.093448   
ee_16                                   0.082864   
ee_17                                   0.124542   
ee_19                                   0.128979   
ee_2                                    0.110003   

            1_0007_the:1_0008_inventor:1_0009_of  \
uniform_id                                         
ee_1                                    0.121588   
ee_16                                   0.070855   
ee_17                                   0.083150   
ee_19                                   0.111848   
ee_2                                    0.081890   

            1_0008_inventor:1_0009_of:1_0010_Morse  \
uniform_id                                           
ee_1                                      0.113608   
ee_16                                     0.099002   
ee_17                                     0.083150   
ee_19                                     0.128205   
ee_2                                      0.125858   

            1_0009_of:1_0010_Morse:1_0011_Code  \
uniform_id                                       
ee_1                                  0.069929   
ee_16                                 0.089695   
ee_17                                 0.143223   
ee_19                                 0.173187   
ee_2                                  0.106407   

            1_0010_Morse:1_0011_Code:1_0012_and  \
uniform_id                                        
ee_1                                   0.082528   
ee_16                                  0.112062   
ee_17                                  0.082051   
ee_19                                  0.155172   
ee_2                                   0.106407   

            1_0011_Code:1_0012_and:1_0013_one  \
uniform_id                                      
ee_1                                 0.090088   
ee_16                                0.074458   
ee_17                                0.082051   
ee_19                                0.096817   
ee_2                                 0.062439   

           

## Apply tags mapper

In [119]:
data_tf_trigrams_POS = map_trigrams(data_tf_trigrams, POS_mapper)
data_tf_trigrams_POS

variable    (ADJ, ADJ, ADJ)  (ADJ, ADJ, CCONJ)  (ADJ, ADJ, NOUN)  \
uniform_id                                                         
ee_1               0.473986           0.335097          0.314606   
ee_16              0.594847           0.293129          0.289133   
ee_17              0.451935           0.287557          0.329299   
ee_19              0.550942           0.421777          0.311216   
ee_2               0.406129           0.271916          0.285424   
...                     ...                ...               ...   
sp_59              0.433248           0.221514          0.319849   
sp_60              0.518463           0.252540          0.338059   
sp_62              0.635911           0.310493          0.271921   
sp_63              0.863065           0.745609          0.337793   
sp_8               0.612195           0.275981          0.336558   

variable    (ADJ, ADP, ADJ)  (ADJ, ADP, DET)  (ADJ, ADP, NOUN)  \
uniform_id                                                       
ee_1               0.086756         0.110801          0.109860   
ee_16              0.084780         0.079395          0.165743   
ee_17              0.134955         0.108477          0.071809   
ee_19              0.098723         0.088206          0.068654   
ee_2               0.162204         0.096762          0.039345   
...                     ...              ...               ...   
sp_59              0.102386         0.083666          0.060488   
sp_60              0.059147         0.126606          0.069080   
sp_62              0.081013         0.053922          0.080288   
sp_63              0.113672         0.108782          0.087946   
sp_8               0.081450         0.076680          0.130833   

variable    (ADJ, ADP, PRON)  (ADJ, ADV, ADP)  (ADJ, ADV, VERB)  \
uniform_id                                                        
ee_1                0.053518         0.102999          0.222693   
ee_16               0.075920         0.081373          0.238797   
ee_17               0.068893         0.033829          0.148950   
ee_19               0.171201         0.038005          0.167092   
ee_2                0.101887         0.050440          0.190513   
...                      ...              ...               ...   
sp_59               0.128322         0.051782          0.146523   
sp_60               0.048817         0.027301          0.095184   
sp_62               0.103376         0.081991          0.191320   
sp_63               0.040525         0.081038          0.305089   
sp_8                0.090570         0.042772          0.172245   

variable    (ADJ, CCONJ, ADJ)  (ADJ, CCONJ, DET)  (ADJ, CCONJ, PRON)  \
uniform_id                                                             
ee_1                 0.233959           0.211079            0.211084   
ee_16                0.239567           0.150544            0.108923   
ee_17                0.288986           0.258328            0.209214   
ee_19                0.255515           0.213553            0.117138   
ee_2                 0.275353           0.105971            0.142588   
...                       ...                ...                 ...   
sp_59                0.291982           0.157917            0.141489   
sp_60                0.254158           0.132989            0.149268   
sp_62                0.237218           0.079278            0.070139   
sp_63                0.321728           0.053920            0.024404   
sp_8                 0.238082           0.062247            0.085745   

variable    (ADJ, DET, PROPN)  (ADJ, DET, VERB)  (ADJ, NOUN, ADJ)  \
uniform_id                                                          
ee_1                 0.218600          0.111748          0.205010   
ee_16                0.273384          0.087006          0.093864   
ee_17                0.552937          0.410605          0.110630   
ee_19                0.272542          0.209318          0.151206   
ee_2                 0.313495    

# Merge to one table

### Fix headers

In [22]:
def add_header(df, header_name):
    """
    header_name - 'TF', 'FF', 'TF_bi', etc.
    """
    header = [[header_name for i in range(len(df.columns))], list(df.columns)]
    df.columns = header
    #return df

In [23]:
add_header(data_tf_bigrams, 'TF_bi')
add_header(data_fp_bigrams, 'FP_bi')
add_header(data_ff_bigrams, 'FF_bi')

add_header(data_tf_trigrams, 'TF_tri')
add_header(data_fp_trigrams, 'FP_tri')
add_header(data_ff_trigrams, 'FF_tri')

In [24]:
# change unigram headers
data_pivoted = data_pivoted.rename(columns={'FP': 'FP_uni', 'FF':'FF_uni', 'TF': 'TF_uni'})
data_pivoted = data_pivoted.drop(['sentences_read'], axis=1) # remove last column sentences read bc all same - 1791 (dunno about the warning msg)

/tmp/ipykernel_3486/2372555628.py:3: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  data_pivoted = data_pivoted.drop(['sentences_read'], axis=1) # remove last column sentences read bc all same - 1791 (dunno about the warning msg)


In [25]:
# check if all len same
len(data_fp_trigrams)

149

### Merge

In [26]:
df_main = data_pivoted.merge(data_tf_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_fp_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_ff_bigrams, on = 'uniform_id')
df_main = df_main.merge(data_tf_trigrams, on = 'uniform_id')
df_main = df_main.merge(data_fp_trigrams, on = 'uniform_id')
df_main = df_main.merge(data_ff_trigrams, on = 'uniform_id')

In [27]:
df_main.shape

(149, 5364)

In [28]:
df_main.head()

TF_uni                                                      \
ia_id      1_0001_Samuel 1_0002_Morse, 1_0003_best 1_0004_known 1_0005_today   
uniform_id                                                                     
ee_1            0.059849      0.044309    0.000000     0.043049     0.045359   
ee_2            0.055410      0.071429    0.029421     0.038411     0.049689   
ee_3            0.109418      0.049126    0.045580     0.026008     0.040063   
ee_12           0.147014      0.099674    0.000000     0.128339     0.000000   
ee_14           0.077373      0.028968    0.054727     0.051047     0.020947   

                                                                        \
ia_id      1_0006_as 1_0007_the 1_0008_inventor 1_0009_of 1_0010_Morse   
uniform_id                                                               
ee_1        0.000000   0.049769        0.043679  0.028139     0.041789   
ee_2        0.028114   0.000000        0.081890  0.000000     0.043969   
ee_3        0.000000   0.032707        0.055037  0.000000     0.034152   
ee_12       0.000000   0.000000        0.062975  0.000000     0.049077   
ee_14       0.000000   0.050104        0.041517  0.025288     0.092753   

                                                                   \
ia_id      1_0011_Code 1_0012_and 1_0013_one 1_0014_of 1_0015_the   
uniform_id                                                          
ee_1          0.000000   0.040739   0.049349  0.000000   0.039899   
ee_2          0.062439   0.000000   0.000000  0.000000   0.050997   
ee_3          0.032839   0.000000   0.031394  0.033233   0.000000   
ee_12         0.031488   0.000000   0.000000  0.046037   0.036265   
ee_14         0.025382   0.000000   0.023495  0.055388   0.000000   

                                                                               \
ia_id      1_0016_inventors 1_0017_of 1_0018_the 1_0019_telegraph, 1_0020_was   
uniform_id                                                                      
ee_1               0.034649  0.039689   0.049139          0.051029   0.019110   
ee_2               0.097581  0.000000   0.024845          0.053449   0.114090   
ee_3               0.056088  0.000000   0.032182          0.067122   0.021017   
ee_12              0.019110  0.000000   0.000000          0.087296   0.000000   
ee_14              0.036799  0.000000   0.023589          0.109360   0.140593   

                                                                         \
ia_id      1_0021_originally  1_0022_a 1_0023_prominent 1_0024_painter.   
uniform_id                                                                
ee_1                0.062789  0.000000         0.143847        0.113818   
ee_2                0.074534  0.000000         0.059660        0.064073   
ee_3                0.058190  0.032182         0.148824        0.094838   
ee_12               0.143322  0.000000         0.105103        0.044300   
ee_14               0.031138  0.000000         0.085582        0.025948   

                                                                              \
ia_id      1_0025_While 1_0026_he 1_0027_was 1_0028_always 1_0029_interested   
uniform_id                                                                     
ee_1           0.040170  0.015013   0.102252      0.081152          0.063806   
ee_2           0.000000  0.018334   0.000000      0.020200          0.018334   
ee_3           0.027784  0.014588   0.016788      0.019427          0.038267   
ee_12          0.000000  0.032554   0.000000      0.000000          0.029271   
ee_14          0.012667  0.000000   0.018269      0.035417          0.016071   

                                                                  \
ia_id      1_0030_in 1_0031_technology 1_0032_and 1_0033_studied   
uniform_id                                                         
ee_1        0.000000          0.046054        0.0       0.044938   
ee_2        0.000000          0.021011        0.0       0.008275   


### save

In [29]:
df_main.to_pickle("../data/df_uni_bi_tri_normalized.pickle")